In [1]:
import torch 

torch.cuda.get_device_name(0)
print(torch.__version__)

torch.cuda.is_available()

1.4.0


True

In [2]:
device = 'cuda:1' if torch.cuda.is_available() else 'cpu' 

torch.manual_seed(123) 
if device =='cuda:1': 
    torch.cuda.manual_seed_all(123)

In [3]:
'''ResNet in PyTorch.
For Pre-activation ResNet, see 'preact_resnet.py'.
Reference:
[1] Kaiming He, Xiangyu Zhang, Shaoqing Ren, Jian Sun
    Deep Residual Learning for Image Recognition. arXiv:1512.03385
'''
import torch
import torch.nn as nn
import torch.nn.functional as F


class BasicBlock(nn.Module):
    expansion = 1

    def __init__(self, in_planes, planes, stride=1):
        super(BasicBlock, self).__init__()
        self.conv1 = nn.Conv2d(
            in_planes, planes, kernel_size=3, stride=stride, padding=1, bias=False)
        self.bn1 = nn.BatchNorm2d(planes)
        
        self.conv2 = nn.Conv2d(planes, planes, kernel_size=3,
                               stride=1, padding=1, bias=False)
        self.bn2 = nn.BatchNorm2d(planes)

        self.shortcut = nn.Sequential()
        
        #stride가 1이아니면
        if stride != 1 or in_planes != self.expansion*planes:
            self.shortcut = nn.Sequential(
                nn.Conv2d(in_planes, self.expansion*planes,
                          kernel_size=1, stride=stride, bias=False),
                nn.BatchNorm2d(self.expansion*planes)
            )

    def forward(self, x):
        out = F.relu(self.bn1(self.conv1(x)))
        out = self.bn2(self.conv2(out))
        out += self.shortcut(x)
        out = F.relu(out)
        return out


    #layer가 50이상일때
class Bottleneck(nn.Module):
    expansion = 4

    def __init__(self, in_planes, planes, stride=1):
        super(Bottleneck, self).__init__()
        self.conv1 = nn.Conv2d(in_planes, planes, kernel_size=1, bias=False)
        self.bn1 = nn.BatchNorm2d(planes)
        
        self.conv2 = nn.Conv2d(planes, planes, kernel_size=3,
                               stride=stride, padding=1, bias=False)
        self.bn2 = nn.BatchNorm2d(planes)
        
        self.conv3 = nn.Conv2d(planes, self.expansion *
                               planes, kernel_size=1, bias=False)
        self.bn3 = nn.BatchNorm2d(self.expansion*planes)

        self.shortcut = nn.Sequential()
        
        if stride != 1 or in_planes != self.expansion*planes:
            self.shortcut = nn.Sequential(
                nn.Conv2d(in_planes, self.expansion*planes,
                          kernel_size=1, stride=stride, bias=False),
                nn.BatchNorm2d(self.expansion*planes)
            )

    def forward(self, x):
        out = F.relu(self.bn1(self.conv1(x)))
        out = F.relu(self.bn2(self.conv2(out)))
        out = self.bn3(self.conv3(out))
        out += self.shortcut(x)
        out = F.relu(out)
        return out


class ResNet(nn.Module):
    def __init__(self, block, num_blocks, num_classes=10):
        super(ResNet, self).__init__()
        self.in_planes = 64

        self.conv1 = nn.Conv2d(3, 64, kernel_size=3,
                               stride=1, padding=1, bias=False)
        self.bn1 = nn.BatchNorm2d(64)
        self.layer1 = self._make_layer(block, 64, num_blocks[0], stride=1)
        self.layer2 = self._make_layer(block, 128, num_blocks[1], stride=2)
        self.layer3 = self._make_layer(block, 256, num_blocks[2], stride=2)
        self.layer4 = self._make_layer(block, 512, num_blocks[3], stride=2)
        self.linear = nn.Linear(512*block.expansion, num_classes)

    def _make_layer(self, block, planes, num_blocks, stride):
        strides = [stride] + [1]*(num_blocks-1)
        layers = []
        for stride in strides:
            layers.append(block(self.in_planes, planes, stride))
            self.in_planes = planes * block.expansion
        return nn.Sequential(*layers)

    def forward(self, x):
        out = F.relu(self.bn1(self.conv1(x)))
        out = self.layer1(out)
        out = self.layer2(out)
        out = self.layer3(out)
        out = self.layer4(out)
        out = F.avg_pool2d(out, 4)
        out = out.view(out.size(0), -1)
        out = self.linear(out)
        return out


def ResNet18():
    return ResNet(BasicBlock, [2, 2, 2, 2])


def ResNet34():
    return ResNet(BasicBlock, [3, 4, 6, 3])


def ResNet50():
    return ResNet(Bottleneck, [3, 4, 6, 3])


def ResNet101():
    return ResNet(Bottleneck, [3, 4, 23, 3])


def ResNet152():
    return ResNet(Bottleneck, [3, 8, 36, 3])


def test():
    net = ResNet18()
    y = net(torch.randn(1, 3, 32, 32))
    print(y.size())

# test()

In [4]:
'''Train CIFAR10 with PyTorch.'''
import torch
import torch.nn as nn
import torch.optim as optim
import torch.nn.functional as F
import torch.backends.cudnn as cudnn

import torchvision
import torchvision.transforms as transforms

import os
import argparse

# from models import *
# from utils import progress_bar


# parser = argparse.ArgumentParser(description='PyTorch CIFAR10 Training')
# parser.add_argument('--lr', default=0.1, type=float, help='learning rate')
# parser.add_argument('--resume', '-r', action='store_true',
#                     help='resume from checkpoint')
# args = parser.parse_args()

device = 'cuda:1' if torch.cuda.is_available() else 'cpu'
best_acc = 0  # best test accuracy
start_epoch = 0  # start from epoch 0 or last checkpoint epoch

# Data
print('==> Preparing data..')
transform_train = transforms.Compose([
    transforms.RandomCrop(32, padding=4),
    transforms.RandomHorizontalFlip(),
    transforms.ToTensor(),
    transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010)),
])

transform_test = transforms.Compose([
    transforms.ToTensor(),
    transforms.Normalize((0.4914, 0.4822, 0.4465), (0.2023, 0.1994, 0.2010)),
])

trainset = torchvision.datasets.CIFAR10(
    root='./data', train=True, download=True, transform=transform_train)
trainloader = torch.utils.data.DataLoader(
    trainset, batch_size=128, shuffle=True, num_workers=2)

testset = torchvision.datasets.CIFAR10(
    root='./data', train=False, download=True, transform=transform_test)

testloader = torch.utils.data.DataLoader(
    testset, batch_size=100, shuffle=False, num_workers=2)

classes = ('plane', 'car', 'bird', 'cat', 'deer',
           'dog', 'frog', 'horse', 'ship', 'truck')

==> Preparing data..
Files already downloaded and verified
Files already downloaded and verified


In [5]:


# Model
print('==> Building model..')

net = ResNet50()

# net = PreActResNet18()
# net = GoogLeNet()
# net = DenseNet121()
# net = ResNeXt29_2x64d()
# net = MobileNet()
# net = MobileNetV2()
# net = DPN92()
# net = ShuffleNetG2()
# net = SENet18()
# net = ShuffleNetV2(1)
# net = EfficientNetB0()
# net = RegNetX_200MF()

net = net.to(device)


# if device == 'cuda:1':
#     net = torch.nn.DataParallel(net)
#     cudnn.benchmark = True

# if args.resume:
#     # Load checkpoint.
#     print('==> Resuming from checkpoint..')
#     assert os.path.isdir('checkpoint'), 'Error: no checkpoint directory found!'
#     checkpoint = torch.load('./checkpoint/ckpt.pth')
#     net.load_state_dict(checkpoint['net'])
#     best_acc = checkpoint['acc']
#     start_epoch = checkpoint['epoch']

criterion = nn.CrossEntropyLoss()
optimizer = optim.SGD(net.parameters(), lr=0.1,
                      momentum=0.9, weight_decay=5e-4)
scheduler = torch.optim.lr_scheduler.CosineAnnealingLR(optimizer, T_max=200)


# Training
def train(epoch):
    print('\nEpoch: %d' % epoch)
    net.train()
    train_loss = 0
    correct = 0
    total = 0
    for batch_idx, (inputs, targets) in enumerate(trainloader):
        inputs, targets = inputs.to(device), targets.to(device)
        optimizer.zero_grad()
        outputs = net(inputs)
        loss = criterion(outputs, targets)
        loss.backward()
        optimizer.step()

        train_loss += loss.item()
        _, predicted = outputs.max(1)
        total += targets.size(0)
        correct += predicted.eq(targets).sum().item()

        print(batch_idx, len(trainloader), 'Loss: %.3f | Acc: %.3f%% (%d/%d)'
                     % (train_loss/(batch_idx+1), 100.*correct/total, correct, total))


def test(epoch):
    global best_acc
    net.eval()
    test_loss = 0
    correct = 0
    total = 0
    with torch.no_grad():
        for batch_idx, (inputs, targets) in enumerate(testloader):
            inputs, targets = inputs.to(device), targets.to(device)
            outputs = net(inputs)
            loss = criterion(outputs, targets)

            test_loss += loss.item()
            _, predicted = outputs.max(1)
            total += targets.size(0)
            correct += predicted.eq(targets).sum().item()

            print(batch_idx, len(testloader), 'Loss: %.3f | Acc: %.3f%% (%d/%d)'
                         % (test_loss/(batch_idx+1), 100.*correct/total, correct, total))

#     # Save checkpoint.
#     acc = 100.*correct/total
#     if acc > best_acc:
#         print('Saving..')
#         state = {
#             'net': net.state_dict(),
#             'acc': acc,
#             'epoch': epoch,
#         }
#         if not os.path.isdir('checkpoint'):
#             os.mkdir('checkpoint')
#         torch.save(state, './checkpoint/ckpt.pth')
#         best_acc = acc


for epoch in range(start_epoch, start_epoch+200):
    train(epoch)
    test(epoch)
    scheduler.step()

==> Building model..

Epoch: 0
0 391 Loss: 2.516 | Acc: 7.031% (9/128)
1 391 Loss: 5.004 | Acc: 10.547% (27/256)
2 391 Loss: 8.332 | Acc: 12.500% (48/384)
3 391 Loss: 10.256 | Acc: 11.914% (61/512)
4 391 Loss: 12.482 | Acc: 11.406% (73/640)
5 391 Loss: 14.935 | Acc: 11.328% (87/768)
6 391 Loss: 14.895 | Acc: 10.491% (94/896)
7 391 Loss: 13.735 | Acc: 10.449% (107/1024)
8 391 Loss: 13.288 | Acc: 10.156% (117/1152)
9 391 Loss: 12.572 | Acc: 9.922% (127/1280)
10 391 Loss: 12.066 | Acc: 10.085% (142/1408)
11 391 Loss: 11.408 | Acc: 9.896% (152/1536)
12 391 Loss: 10.923 | Acc: 9.916% (165/1664)
13 391 Loss: 10.375 | Acc: 10.100% (181/1792)
14 391 Loss: 9.944 | Acc: 10.469% (201/1920)
15 391 Loss: 9.626 | Acc: 10.449% (214/2048)
16 391 Loss: 9.377 | Acc: 10.570% (230/2176)
17 391 Loss: 9.088 | Acc: 10.503% (242/2304)
18 391 Loss: 8.866 | Acc: 10.609% (258/2432)
19 391 Loss: 8.642 | Acc: 10.508% (269/2560)
20 391 Loss: 8.422 | Acc: 10.305% (277/2688)
21 391 Loss: 8.182 | Acc: 10.298% (290/281

176 391 Loss: 3.146 | Acc: 13.617% (3085/22656)
177 391 Loss: 3.140 | Acc: 13.650% (3110/22784)
178 391 Loss: 3.134 | Acc: 13.678% (3134/22912)
179 391 Loss: 3.128 | Acc: 13.702% (3157/23040)
180 391 Loss: 3.122 | Acc: 13.722% (3179/23168)
181 391 Loss: 3.116 | Acc: 13.753% (3204/23296)
182 391 Loss: 3.110 | Acc: 13.828% (3239/23424)
183 391 Loss: 3.105 | Acc: 13.876% (3268/23552)
184 391 Loss: 3.100 | Acc: 13.910% (3294/23680)
185 391 Loss: 3.095 | Acc: 13.949% (3321/23808)
186 391 Loss: 3.091 | Acc: 13.991% (3349/23936)
187 391 Loss: 3.086 | Acc: 14.004% (3370/24064)
188 391 Loss: 3.080 | Acc: 14.038% (3396/24192)
189 391 Loss: 3.074 | Acc: 14.091% (3427/24320)
190 391 Loss: 3.070 | Acc: 14.116% (3451/24448)
191 391 Loss: 3.065 | Acc: 14.176% (3484/24576)
192 391 Loss: 3.059 | Acc: 14.241% (3518/24704)
193 391 Loss: 3.054 | Acc: 14.276% (3545/24832)
194 391 Loss: 3.049 | Acc: 14.307% (3571/24960)
195 391 Loss: 3.044 | Acc: 14.349% (3600/25088)
196 391 Loss: 3.039 | Acc: 14.356% (3620

348 391 Loss: 2.590 | Acc: 18.707% (8357/44672)
349 391 Loss: 2.588 | Acc: 18.730% (8391/44800)
350 391 Loss: 2.587 | Acc: 18.759% (8428/44928)
351 391 Loss: 2.585 | Acc: 18.783% (8463/45056)
352 391 Loss: 2.583 | Acc: 18.801% (8495/45184)
353 391 Loss: 2.581 | Acc: 18.845% (8539/45312)
354 391 Loss: 2.579 | Acc: 18.869% (8574/45440)
355 391 Loss: 2.578 | Acc: 18.893% (8609/45568)
356 391 Loss: 2.576 | Acc: 18.912% (8642/45696)
357 391 Loss: 2.574 | Acc: 18.933% (8676/45824)
358 391 Loss: 2.572 | Acc: 18.961% (8713/45952)
359 391 Loss: 2.570 | Acc: 19.000% (8755/46080)
360 391 Loss: 2.568 | Acc: 19.021% (8789/46208)
361 391 Loss: 2.566 | Acc: 19.039% (8822/46336)
362 391 Loss: 2.564 | Acc: 19.049% (8851/46464)
363 391 Loss: 2.562 | Acc: 19.072% (8886/46592)
364 391 Loss: 2.561 | Acc: 19.101% (8924/46720)
365 391 Loss: 2.559 | Acc: 19.134% (8964/46848)
366 391 Loss: 2.557 | Acc: 19.157% (8999/46976)
367 391 Loss: 2.555 | Acc: 19.194% (9041/47104)
368 391 Loss: 2.554 | Acc: 19.224% (9080

36 391 Loss: 1.843 | Acc: 30.258% (1433/4736)
37 391 Loss: 1.841 | Acc: 30.325% (1475/4864)
38 391 Loss: 1.842 | Acc: 30.148% (1505/4992)
39 391 Loss: 1.841 | Acc: 30.176% (1545/5120)
40 391 Loss: 1.841 | Acc: 30.335% (1592/5248)
41 391 Loss: 1.842 | Acc: 30.450% (1637/5376)
42 391 Loss: 1.838 | Acc: 30.687% (1689/5504)
43 391 Loss: 1.834 | Acc: 30.895% (1740/5632)
44 391 Loss: 1.833 | Acc: 31.007% (1786/5760)
45 391 Loss: 1.834 | Acc: 31.046% (1828/5888)
46 391 Loss: 1.834 | Acc: 31.084% (1870/6016)
47 391 Loss: 1.833 | Acc: 31.234% (1919/6144)
48 391 Loss: 1.831 | Acc: 31.234% (1959/6272)
49 391 Loss: 1.829 | Acc: 31.188% (1996/6400)
50 391 Loss: 1.830 | Acc: 31.219% (2038/6528)
51 391 Loss: 1.828 | Acc: 31.280% (2082/6656)
52 391 Loss: 1.825 | Acc: 31.397% (2130/6784)
53 391 Loss: 1.827 | Acc: 31.409% (2171/6912)
54 391 Loss: 1.826 | Acc: 31.364% (2208/7040)
55 391 Loss: 1.826 | Acc: 31.348% (2247/7168)
56 391 Loss: 1.826 | Acc: 31.332% (2286/7296)
57 391 Loss: 1.827 | Acc: 31.304% 

210 391 Loss: 1.746 | Acc: 34.875% (9419/27008)
211 391 Loss: 1.746 | Acc: 34.895% (9469/27136)
212 391 Loss: 1.746 | Acc: 34.925% (9522/27264)
213 391 Loss: 1.745 | Acc: 34.955% (9575/27392)
214 391 Loss: 1.745 | Acc: 34.956% (9620/27520)
215 391 Loss: 1.745 | Acc: 34.972% (9669/27648)
216 391 Loss: 1.745 | Acc: 34.955% (9709/27776)
217 391 Loss: 1.745 | Acc: 34.952% (9753/27904)
218 391 Loss: 1.745 | Acc: 34.932% (9792/28032)
219 391 Loss: 1.745 | Acc: 34.904% (9829/28160)
220 391 Loss: 1.744 | Acc: 34.955% (9888/28288)
221 391 Loss: 1.744 | Acc: 34.938% (9928/28416)
222 391 Loss: 1.743 | Acc: 34.981% (9985/28544)
223 391 Loss: 1.742 | Acc: 34.992% (10033/28672)
224 391 Loss: 1.742 | Acc: 34.990% (10077/28800)
225 391 Loss: 1.742 | Acc: 35.001% (10125/28928)
226 391 Loss: 1.742 | Acc: 34.977% (10163/29056)
227 391 Loss: 1.742 | Acc: 34.978% (10208/29184)
228 391 Loss: 1.741 | Acc: 34.992% (10257/29312)
229 391 Loss: 1.741 | Acc: 35.017% (10309/29440)
230 391 Loss: 1.741 | Acc: 35.034

...

252 391 Loss: 0.001 | Acc: 99.997% (32383/32384)
253 391 Loss: 0.001 | Acc: 99.997% (32511/32512)
254 391 Loss: 0.001 | Acc: 99.997% (32639/32640)
255 391 Loss: 0.001 | Acc: 99.997% (32767/32768)
256 391 Loss: 0.001 | Acc: 99.997% (32895/32896)
257 391 Loss: 0.001 | Acc: 99.997% (33023/33024)
258 391 Loss: 0.001 | Acc: 99.997% (33151/33152)
259 391 Loss: 0.001 | Acc: 99.997% (33279/33280)
260 391 Loss: 0.001 | Acc: 99.997% (33407/33408)
261 391 Loss: 0.001 | Acc: 99.997% (33535/33536)
262 391 Loss: 0.001 | Acc: 99.997% (33663/33664)
263 391 Loss: 0.001 | Acc: 99.997% (33791/33792)
264 391 Loss: 0.001 | Acc: 99.997% (33919/33920)
265 391 Loss: 0.001 | Acc: 99.997% (34047/34048)
266 391 Loss: 0.001 | Acc: 99.997% (34175/34176)
267 391 Loss: 0.001 | Acc: 99.997% (34303/34304)
268 391 Loss: 0.001 | Acc: 99.997% (34431/34432)
269 391 Loss: 0.001 | Acc: 99.997% (34559/34560)
270 391 Loss: 0.001 | Acc: 99.997% (34687/34688)
271 391 Loss: 0.001 | Acc: 99.997% (34815/34816)
272 391 Loss: 0.001 

36 100 Loss: 0.201 | Acc: 95.108% (3519/3700)
37 100 Loss: 0.202 | Acc: 95.026% (3611/3800)
38 100 Loss: 0.199 | Acc: 95.128% (3710/3900)
39 100 Loss: 0.197 | Acc: 95.150% (3806/4000)
40 100 Loss: 0.198 | Acc: 95.122% (3900/4100)
41 100 Loss: 0.197 | Acc: 95.095% (3994/4200)
42 100 Loss: 0.197 | Acc: 95.093% (4089/4300)
43 100 Loss: 0.195 | Acc: 95.136% (4186/4400)
44 100 Loss: 0.193 | Acc: 95.200% (4284/4500)
45 100 Loss: 0.195 | Acc: 95.130% (4376/4600)
46 100 Loss: 0.199 | Acc: 95.085% (4469/4700)
47 100 Loss: 0.204 | Acc: 94.958% (4558/4800)
48 100 Loss: 0.200 | Acc: 95.061% (4658/4900)
49 100 Loss: 0.205 | Acc: 94.980% (4749/5000)
50 100 Loss: 0.202 | Acc: 95.020% (4846/5100)
51 100 Loss: 0.202 | Acc: 95.058% (4943/5200)
52 100 Loss: 0.200 | Acc: 95.094% (5040/5300)
53 100 Loss: 0.198 | Acc: 95.130% (5137/5400)
54 100 Loss: 0.199 | Acc: 95.127% (5232/5500)
55 100 Loss: 0.199 | Acc: 95.161% (5329/5600)
56 100 Loss: 0.198 | Acc: 95.175% (5425/5700)
57 100 Loss: 0.196 | Acc: 95.207% 

112 391 Loss: 0.001 | Acc: 99.993% (14463/14464)
113 391 Loss: 0.001 | Acc: 99.993% (14591/14592)
114 391 Loss: 0.001 | Acc: 99.993% (14719/14720)
115 391 Loss: 0.001 | Acc: 99.993% (14847/14848)
116 391 Loss: 0.001 | Acc: 99.993% (14975/14976)
117 391 Loss: 0.001 | Acc: 99.993% (15103/15104)
118 391 Loss: 0.001 | Acc: 99.993% (15231/15232)
119 391 Loss: 0.001 | Acc: 99.993% (15359/15360)
120 391 Loss: 0.001 | Acc: 99.994% (15487/15488)
121 391 Loss: 0.001 | Acc: 99.994% (15615/15616)
122 391 Loss: 0.001 | Acc: 99.994% (15743/15744)
123 391 Loss: 0.001 | Acc: 99.994% (15871/15872)
124 391 Loss: 0.001 | Acc: 99.994% (15999/16000)
125 391 Loss: 0.001 | Acc: 99.994% (16127/16128)
126 391 Loss: 0.001 | Acc: 99.994% (16255/16256)
127 391 Loss: 0.001 | Acc: 99.994% (16383/16384)
128 391 Loss: 0.001 | Acc: 99.994% (16511/16512)
129 391 Loss: 0.001 | Acc: 99.994% (16639/16640)
130 391 Loss: 0.001 | Acc: 99.994% (16767/16768)
131 391 Loss: 0.001 | Acc: 99.994% (16895/16896)
132 391 Loss: 0.001 

280 391 Loss: 0.001 | Acc: 99.997% (35967/35968)
281 391 Loss: 0.001 | Acc: 99.997% (36095/36096)
282 391 Loss: 0.001 | Acc: 99.997% (36223/36224)
283 391 Loss: 0.001 | Acc: 99.997% (36351/36352)
284 391 Loss: 0.001 | Acc: 99.997% (36479/36480)
285 391 Loss: 0.001 | Acc: 99.997% (36607/36608)
286 391 Loss: 0.001 | Acc: 99.997% (36735/36736)
287 391 Loss: 0.001 | Acc: 99.997% (36863/36864)
288 391 Loss: 0.001 | Acc: 99.997% (36991/36992)
289 391 Loss: 0.001 | Acc: 99.997% (37119/37120)
290 391 Loss: 0.001 | Acc: 99.997% (37247/37248)
291 391 Loss: 0.001 | Acc: 99.997% (37375/37376)
292 391 Loss: 0.001 | Acc: 99.997% (37503/37504)
293 391 Loss: 0.001 | Acc: 99.997% (37631/37632)
294 391 Loss: 0.001 | Acc: 99.997% (37759/37760)
295 391 Loss: 0.001 | Acc: 99.997% (37887/37888)
296 391 Loss: 0.001 | Acc: 99.997% (38015/38016)
297 391 Loss: 0.001 | Acc: 99.997% (38143/38144)
298 391 Loss: 0.001 | Acc: 99.997% (38271/38272)
299 391 Loss: 0.001 | Acc: 99.997% (38399/38400)
300 391 Loss: 0.001 

66 100 Loss: 0.187 | Acc: 95.433% (6394/6700)
67 100 Loss: 0.189 | Acc: 95.397% (6487/6800)
68 100 Loss: 0.191 | Acc: 95.348% (6579/6900)
69 100 Loss: 0.190 | Acc: 95.357% (6675/7000)
70 100 Loss: 0.193 | Acc: 95.324% (6768/7100)
71 100 Loss: 0.193 | Acc: 95.319% (6863/7200)
72 100 Loss: 0.192 | Acc: 95.342% (6960/7300)
73 100 Loss: 0.192 | Acc: 95.365% (7057/7400)
74 100 Loss: 0.194 | Acc: 95.347% (7151/7500)
75 100 Loss: 0.194 | Acc: 95.329% (7245/7600)
76 100 Loss: 0.194 | Acc: 95.312% (7339/7700)
77 100 Loss: 0.193 | Acc: 95.346% (7437/7800)
78 100 Loss: 0.195 | Acc: 95.316% (7530/7900)
79 100 Loss: 0.194 | Acc: 95.312% (7625/8000)
80 100 Loss: 0.193 | Acc: 95.346% (7723/8100)
81 100 Loss: 0.193 | Acc: 95.366% (7820/8200)
82 100 Loss: 0.194 | Acc: 95.349% (7914/8300)
83 100 Loss: 0.193 | Acc: 95.357% (8010/8400)
84 100 Loss: 0.193 | Acc: 95.353% (8105/8500)
85 100 Loss: 0.194 | Acc: 95.314% (8197/8600)
86 100 Loss: 0.193 | Acc: 95.310% (8292/8700)
87 100 Loss: 0.194 | Acc: 95.307% 

In [6]:
!nvidia-smi

Wed Oct  6 17:52:31 2021       
+-----------------------------------------------------------------------------+
| NVIDIA-SMI 418.67       Driver Version: 418.67       CUDA Version: 10.1     |
|-------------------------------+----------------------+----------------------+
| GPU  Name        Persistence-M| Bus-Id        Disp.A | Volatile Uncorr. ECC |
| Fan  Temp  Perf  Pwr:Usage/Cap|         Memory-Usage | GPU-Util  Compute M. |
|===============================+======================+======================|
|   0  Tesla V100-SXM2...  On   | 00000000:00:05.0 Off |                  Off |
| N/A   53C    P0   107W / 300W |  31611MiB / 32480MiB |     53%      Default |
+-------------------------------+----------------------+----------------------+
|   1  Tesla V100-SXM2...  On   | 00000000:00:06.0 Off |                  Off |
| N/A   61C    P0    71W / 300W |   6411MiB / 32480MiB |      0%      Default |
+-------------------------------+----------------------+----------------------+
        